# Preprocessing and Training Data Development

The goal in this notebook is to complete <a href=https://aiden-dataminer.medium.com/the-data-science-method-dsm-pre-processing-and-training-data-development-fd2d75182967>step 4 of the data science method</a>: split my data into test and train sets, prepare the data for modeling by handling any categorical variables appropriately and scaling any numerical features appropriately.



### Completion Criteria:
Every step identified in the DSM has been addressed or completed, including:
 1. Creating dummy features
 2. Scale standardization
 3. Split data into training and testing subsets


In [1]:
#import standard libraries 
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
import numpy as np

## Evaluating the training and testing data sets

The data for this project was downloaded from <a href="https://www.kaggle.com/datasets/kaushil268/disease-prediction-using-machine-learning">Kaggle</a>, and came pre-split into testing and training sets. 

I'm going to load them now to evaluate how the size of each set compares to each other.

In [2]:
train_data = pd.read_csv('data.csv')
train_data.shape

(4920, 133)

In [3]:
test_data = pd.read_csv('Testing.csv')
test_data.shape

(42, 133)

The training data contains 4920 observations while the testing data contains just 42 observations, just 0.8% of the overall data available. I think Kaggle datasets are often set up like this to have the test data mimic incoming new data and to have a standard by which to evaluate the final model performance between Data Scientists. 

I have a choice: I could split the training data into something more like 80:20 train:test and augment the current test_data set to evaluate final model performance. This would be more in-line with standard DS practice.

Or, I could keep the small test_data provided by the Kaggle creator separate as the *final* model performance metric, and internally divide the training set into train and test sets to use for cross validation and internal model performance metrics.

I think I'll go with option 2. This will give me two data sets with which to evaluate the models I try: 1 set of internal metrics to rigorously compare the models and 1 set of performance metrics to share on Kaggle to be easily compared to the results of others who have worked with this data set.

In [4]:
#rename test_data to final_test_data, as the comparative performance metric to share on Kaggle
final_test_data = test_data

Before I split my training data, I first want to evaluate which features may need to be transformed to be ready for modeling.

## Preprocessing for Modeling Readiness

Let's take a look once more at the train_data df to see columns and data types

In [5]:
train_data.dtypes

itching                  int64
skin_rash                int64
nodal_skin_eruptions     int64
continuous_sneezing      int64
shivering                int64
                         ...  
inflammatory_nails       int64
blister                  int64
red_sore_around_nose     int64
yellow_crust_ooze        int64
prognosis               object
Length: 133, dtype: object

In [6]:
train_data.head()

itching  skin_rash  nodal_skin_eruptions  continuous_sneezing  shivering  \
0        1          1                     1                    0          0   
1        0          1                     1                    0          0   
2        1          0                     1                    0          0   
3        1          1                     0                    0          0   
4        1          1                     1                    0          0   

   chills  joint_pain  stomach_pain  acidity  ulcers_on_tongue  ...  \
0       0           0             0        0                 0  ...   
1       0           0             0        0                 0  ...   
2       0           0             0        0                 0  ...   
3       0           0             0        0                 0  ...   
4       0           0             0        0                 0  ...   

   blackheads  scurring  skin_peeling  silver_like_dusting  \
0           0         0             0                    0   
1           0         0             0                    0   
2           0         0             0                    0   
3           0         0             0                    0   
4           0         0             0                    0   

   small_dents_in_nails  inflammatory_nails  blister  red_sore_around_nose  \
0                     0                   0        0                     0   
1                     0                   0        0                     0   
2                     0                   0        0                     0   
3                     0                   0        0                     0   
4                     0                   0        0                     0   

   yellow_crust_ooze         prognosis  
0                  0  Fungal infection  
1                  0  Fungal infection  
2                  0  Fungal infection  
3                  0  Fungal infection  
4                  0  Fungal infection  

[5 rows x 133 columns]

Our independent variables (the 133 symptoms tracked in the data set) are of type int64, and are already formatted as binary values.

Our target (dependent) variable is the categorical feature "prognosis." In theory, for classification ML models this feature should not need to be changed. Let's give it a quick try to see

In [7]:
from sklearn import tree, metrics
from sklearn.model_selection import train_test_split

#split data into X and y
X = train_data.drop(columns='prognosis')
y = train_data['prognosis']

#split X and y into training and testing
X_train, X_test, y_train, y_test = train_test_split(X , y, test_size=0.2, random_state=42)

# Declare a variable called entr_model and use tree.DecisionTreeClassifier. 
entr_model = tree.DecisionTreeClassifier(criterion = 'entropy', random_state=42)

# Call fit() on entr_model, and pass in X_train and y_train, in that order 
entr_model.fit(X_train, y_train)

# Call predict() on entr_model with X_test passed to it, and assign the result to a variable y_pred 
y_pred = entr_model.predict(X_test)

# Assign y_pred the following: pd.Series(y_pred)
y_pred = pd.Series(y_pred)

# Check out entr_model
entr_model

DecisionTreeClassifier(criterion='entropy', random_state=42)

In [8]:
from sklearn import tree, metrics
from sklearn.model_selection import train_test_split
import matplotlib.pyplot as plt
from io import StringIO  
from IPython.display import Image  
import pydotplus
import graphviz

# Now we want to visualize the tree
dot_data = StringIO()

# We can do so with export_graphviz
tree.export_graphviz(entr_model, out_file=dot_data,  
                filled=True, rounded=True,
                special_characters=True, feature_names=X_train.columns, class_names = entr_model.classes_)
graph = graphviz.Source(dot_data)
graph

# Alternatively for class_names use entr_model.classes_
graph = pydotplus.graph_from_dot_data(dot_data.getvalue())  
Image(graph.create_png())

Woah--that's a deep tree! Out of curiousity, I'll just get the performance metrics...

In [9]:
# Run this block for model evaluation metrics 
print("Model Entropy - no max depth")
print("Accuracy:", metrics.accuracy_score(y_test,y_pred))
print("Balanced accuracy:", metrics.balanced_accuracy_score(y_test,y_pred))
print('Precision score for by category' , metrics.precision_score(y_test,y_pred, average=None))


Model Entropy - no max depth
Accuracy: 1.0
Balanced accuracy: 1.0
Precision score for by category [1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1.
 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1.]


Ok, so the super deep tree gives perfect accuracy and precision! Haha, no big surprise there. This is way overfit, but that's really not the purpose of this notebook. This excercise was simply to see if keeping my y as an unencoded category would work and the answer is....yes!

## Save testing and training sets for use in modeling, the next notebook

In [10]:
X_final_test = final_test_data.drop(columns='prognosis')
y_final_test = final_test_data['prognosis']

In [11]:
X_train.to_csv('X_train.csv', index=False)
X_test.to_csv('X_test.csv', index=False)
y_train.to_csv('y_train.csv', index=False)
y_test.to_csv('y_test.csv', index=False)
X_final_test.to_csv('X_final_test.csv', index=False)
y_final_test.to_csv('y_final_test.csv', index=False)

These should be ready to go for modeling!